### Step1. GPU 사용현황 체크 ###
하기 메모리 사용량이 1MiB가 아니라면 해당 인스턴스 내에서 GPU를 사용하는 작업이 이미 돌아가고 있다는 의미임.

In [1]:
!nvidia-smi

Thu Jul 24 23:04:20 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.163.01             Driver Version: 550.163.01     CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A10G                    On  |   00000000:00:1E.0 Off |                    0 |
|  0%   35C    P8             16W /  300W |       1MiB /  23028MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

### ComfyUI 기본 환경 구축 ###
이 셀은 ComfyUI를 실행하는 데 필요한 모든 기본 프로그램을 설치하고 환경을 설정하는 역할을 합니다. 스크립트는 크게 네 부분으로 구성되어 있습니다.

1. Git 및 Git-LFS 설치

git: ComfyUI의 소스 코드를 GitHub에서 다운로드하기 위해 필요한 버전 관리 도구입니다.

git-lfs: AI 모델과 같은 수 기가바이트(GB)에 달하는 대용량 파일을 다운로드하기 위한 필수 확장 프로그램입니다.

코드는 이 두 프로그램이 이미 설치되어 있는지 확인하고, 없을 경우에만 자동으로 설치를 진행하여 시간을 절약합니다.

2. ComfyUI 설치

git clone 명령어를 사용하여 GitHub에서 ComfyUI의 최신 소스 코드를 다운로드합니다.

다운로드된 파일들은 현재 디렉토리 아래 ComfyUI라는 폴더에 저장됩니다.

3. 필수 파이썬 라이브러리 설치

ComfyUI가 정상적으로 작동하기 위해 필요한 여러 파이썬 라이브러리(PyTorch, NumPy 등)들을 설치합니다.

requirements.txt 파일은 필요한 라이브러리 목록이 적힌 '설치 설명서'와 같으며, 이 파일을 이용해 한 번에 설치를 진행합니다.

4. ComfyUI-Manager 설치

ComfyUI의 필수 확장 기능인 ComfyUI-Manager를 설치합니다.

이 매니저를 통해 이후 필요한 커스텀 노드나 모델들을 ComfyUI 인터페이스 내에서 클릭 몇 번으로 쉽게 검색하고 설치할 수 있어 매우 편리합니다.

결론적으로 이 셀을 실행하면, 사용자는 복잡한 설치 과정을 거치지 않고 ComfyUI를 구동할 준비가 된 깨끗한 기본 환경을 갖추게 됩니다.

In [2]:
# --- 셀 1: 기본 환경 설정 및 ComfyUI 설치 ---
import os
import sys
import subprocess

# !git 및 git-lfs 설치 (SageMaker 환경에 기본적으로 없을 경우)
print(">>> Git 및 Git-LFS 설치 확인...")
try:
    subprocess.run(["git", "--version"], check=True, capture_output=True)
    subprocess.run(["git-lfs", "--version"], check=True, capture_output=True)
    print(">>> Git 및 Git-LFS가 이미 설치되어 있습니다.")
except (subprocess.CalledProcessError, FileNotFoundError):
    print(">>> Git 또는 Git-LFS가 설치되어 있지 않습니다. 설치를 시작합니다.")
    subprocess.run([sys.executable, '-m', 'pip', 'install', 'gitpython'], check=True)
    # conda를 사용하여 git-lfs 설치
    subprocess.run(['conda', 'install', '-c', 'conda-forge', 'git-lfs', '-y'], check=True)
    subprocess.run(['git-lfs', 'install'], check=True)
    print(">>> Git 및 Git-LFS 설치 완료.")


# ComfyUI 설치
COMFYUI_DIR = os.path.join(os.getcwd(), "ComfyUI")
if not os.path.exists(COMFYUI_DIR):
    print(f">>> ComfyUI를 '{COMFYUI_DIR}'에 클론합니다...")
    subprocess.run(["git", "clone", "https://github.com/comfyanonymous/ComfyUI.git"], check=True)
    print(">>> ComfyUI 클론 완료.")
else:
    print(f">>> ComfyUI가 이미 '{COMFYUI_DIR}'에 존재합니다.")

# 필요한 파이썬 라이브러리 설치
print(">>> 필수 파이썬 라이브러리를 설치합니다...")
%cd {COMFYUI_DIR}
subprocess.run([sys.executable, '-m', 'pip', 'install', '-r', 'requirements.txt'], check=True)
subprocess.run([sys.executable, '-m', 'pip', 'install', 'websocket-client', 'requests', 'numpy', 'Pillow', 'opencv-python'], check=True)
print(">>> 라이브러리 설치 완료.")

# ComfyUI-Manager 설치 (모델 관리를 용이하게 함)
MANAGER_DIR = os.path.join(COMFYUI_DIR, "custom_nodes", "ComfyUI-Manager")
if not os.path.exists(MANAGER_DIR):
    print(">>> ComfyUI-Manager를 설치합니다...")
    subprocess.run(["git", "clone", "https://github.com/ltdrdata/ComfyUI-Manager.git", MANAGER_DIR], check=True)
    manager_req_path = os.path.join(MANAGER_DIR, "requirements.txt")
    if os.path.exists(manager_req_path):
        subprocess.run([sys.executable, '-m', 'pip', 'install', '-r', manager_req_path], check=True)
    print(">>> ComfyUI-Manager 설치 완료.")
else:
    print(">>> ComfyUI-Manager가 이미 설치되어 있습니다.")

%cd ..
print("\n--- 환경 설정이 완료되었습니다. ---")

>>> Git 및 Git-LFS 설치 확인...
>>> Git 및 Git-LFS가 이미 설치되어 있습니다.
>>> ComfyUI가 이미 '/home/sagemaker-user/ComfyUI'에 존재합니다.
>>> 필수 파이썬 라이브러리를 설치합니다...
/home/sagemaker-user/ComfyUI
>>> 라이브러리 설치 완료.
>>> ComfyUI-Manager가 이미 설치되어 있습니다.
/home/sagemaker-user

--- 환경 설정이 완료되었습니다. ---


### AI 모델 다운로드 및 준비 ###
이 셀은 ComfyUI 워크플로우에서 이미지를 생성하는 데 실질적으로 사용될 다양한 AI 모델들을 다운로드하고, 정해진 위치에 배치하는 역할을 합니다.

1. 폴더 구조 생성

ComfyUI는 모델의 종류에 따라 정해진 폴더에 저장해야 제대로 인식할 수 있습니다. 이 스크립트는 AI 모델을 저장할 다음과 같은 하위 폴더들을 ComfyUI/models/ 디렉토리 내에 자동으로 생성합니다.

checkpoints: 이미지 생성의 근간이 되는 핵심 모델 폴더

controlnet: 이미지의 구도나 자세를 제어하는 모델 폴더

ipadapter: 다른 이미지의 스타일을 복사해오는 모델 폴더

loras: 특정 캐릭터나 화풍을 추가하는 소형 모델 폴더

upscale_models: 이미지 해상도를 높이는 모델 폴더

2. 다운로드 자동화 (download_model 함수)

스크립트는 모델 다운로드를 자동화하는 download_model 함수를 정의합니다. 이 함수는 다음과 같은 스마트한 기능을 포함합니다.

중복 방지: 다운로드 전에 파일이 이미 존재하는지 확인하여, 불필요한 재다운로드를 방지합니다.

자동 다운로드: 파일이 없을 경우에만 wget 명령어를 사용해 지정된 URL에서 모델을 다운로드합니다.

3. 주요 모델 다운로드

스크립트는 위 함수를 이용해 워크플로우에 필요한 핵심 모델들을 다운로드합니다.

① 체크포인트 (Checkpoint): 그림을 그리는 화가(👨‍🎨)의 역할을 하는 가장 기본적이고 중요한 모델입니다. 예시에서는 사실적인 표현에 강점이 있는 Juggernaut XL 모델을 다운로드합니다.

② 컨트롤넷 (ControlNet): 이미지의 구도, 깊이감, 윤곽선 등을 제어하여 사용자가 원하는 결과물을 더 정교하게 만들도록 돕는 보조 모델입니다.

③ IP-Adapter: 다른 이미지의 스타일(색감, 분위기, 질감 등)을 가져와 새로 생성되는 이미지에 적용하는 모델입니다. CLIP Vision 모델은 IP-Adapter가 참조 이미지의 스타일을 "인식"하기 위해 필요한 눈(👁️) 역할을 합니다.

④ 업스케일 (Upscale): 생성된 이미지의 해상도를 품질 저하 없이 높여주는 후반 작업용 모델입니다.

결론적으로 이 셀을 실행하면, 이미지 생성에 필요한 모든 '재료(모델)'들이 준비되어 ComfyUI가 즉시 작업을 수행할 수 있는 상태가 됩니다.

In [18]:
# --- 셀 2: 워크플로우에 필요한 모델 다운로드 ---
import os
import subprocess

# 모델을 저장할 디렉토리 경로 설정
CHECKPOINT_DIR = os.path.join(COMFYUI_DIR, "models", "checkpoints")
CONTROLNET_DIR = os.path.join(COMFYUI_DIR, "models", "controlnet")
IPADAPTER_DIR = os.path.join(COMFYUI_DIR, "models", "ipadapter")
CLIP_VISION_DIR = os.path.join(COMFYUI_DIR, "models", "clip_vision")
LORA_DIR = os.path.join(COMFYUI_DIR, "models", "loras")
UPSCALE_DIR = os.path.join(COMFYUI_DIR, "models", "upscale_models")

# 디렉토리 생성
os.makedirs(CHECKPOINT_DIR, exist_ok=True)
os.makedirs(CONTROLNET_DIR, exist_ok=True)
os.makedirs(IPADAPTER_DIR, exist_ok=True)
os.makedirs(CLIP_VISION_DIR, exist_ok=True)
os.makedirs(LORA_DIR, exist_ok=True)
os.makedirs(UPSCALE_DIR, exist_ok=True)

# 다운로드 함수
def download_model(url, dest_dir):
    filename = url.split('/')[-1]
    dest_path = os.path.join(dest_dir, filename)
    if not os.path.exists(dest_path):
        print(f">>> '{filename}' 다운로드 중...")
        subprocess.run(["wget", "-c", url, "-O", dest_path], check=True)
        print(f">>> '{filename}' 다운로드 완료.")
    else:
        print(f">>> '{filename}'이(가) 이미 존재합니다.")

# 1. SDXL 체크포인트 모델 
download_model("https://huggingface.co/Lykon/dreamshaper-xl-lightning/resolve/main/DreamShaperXL_Lightning.safetensors", CHECKPOINT_DIR)
download_model("https://huggingface.co/SG161222/RealVisXL_V4.0/resolve/main/RealVisXL_V4.0.safetensors", CHECKPOINT_DIR)
download_model("https://huggingface.co/RunDiffusion/Juggernaut-XL/resolve/main/juggernautXL_version2.safetensors", CHECKPOINT_DIR)
download_model("https://huggingface.co/cyberdelia/CyberRealisticXL/resolve/main/CyberRealisticXLPlay_V6.0.safetensors", CHECKPOINT_DIR)

# 2. ControlNet 모델 (Depth 및 Canny)
#download_model("https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11f1p_sd15_depth_fp16.safetensors", CONTROLNET_DIR)
#download_model("https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_canny_fp16.safetensors", CONTROLNET_DIR)
#download_model("https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_inpaint_fp16.safetensors", CONTROLNET_DIR)

download_model("https://huggingface.co/xinsir/controlnet-union-sdxl-1.0/resolve/main/diffusion_pytorch_model.safetensors", CONTROLNET_DIR)
download_model("https://huggingface.co/xinsir/controlnet-union-sdxl-1.0/resolve/main/diffusion_pytorch_model_promax.safetensors", CONTROLNET_DIR)

# 3. IP-Adapter 모델
download_model("https://huggingface.co/h94/IP-Adapter/resolve/main/sdxl_models/ip-adapter-plus_sdxl_vit-h.safetensors", IPADAPTER_DIR)
#download_model("https://huggingface.co/h94/IP-Adapter/resolve/main/models/ip-adapter_sd15.bin", IPADAPTER_DIR)

# CLIP Vision Encoder
#download_model("https://huggingface.co/h94/IP-Adapter/tree/main/image_encoder", CLIP_VISION_DIR)
download_model("https://huggingface.co/laion/CLIP-ViT-H-14-laion2B-s32B-b79K/resolve/main/model.safetensors", CLIP_VISION_DIR)

# 4. 업스케일 모델 (4x-UltraSharp)
download_model("https://huggingface.co/lokCX/4x-UltraSharp/resolve/main/4x-UltraSharp.pth", UPSCALE_DIR)

print("\n--- 모든 모델 다운로드가 완료되었습니다. ---")

>>> 'DreamShaperXL_Lightning.safetensors'이(가) 이미 존재합니다.
>>> 'RealVisXL_V4.0.safetensors'이(가) 이미 존재합니다.
>>> 'juggernautXL_version2.safetensors'이(가) 이미 존재합니다.
>>> 'CyberRealisticXLPlay_V6.0.safetensors'이(가) 이미 존재합니다.
>>> 'diffusion_pytorch_model.safetensors'이(가) 이미 존재합니다.
>>> 'diffusion_pytorch_model_promax.safetensors'이(가) 이미 존재합니다.
>>> 'ip-adapter-plus_sdxl_vit-h.safetensors'이(가) 이미 존재합니다.
>>> 'model.safetensors' 다운로드 중...


--2025-07-25 01:31:03--  https://huggingface.co/laion/CLIP-ViT-H-14-laion2B-s32B-b79K/resolve/main/model.safetensors
Resolving huggingface.co (huggingface.co)... 3.167.112.96, 3.167.112.25, 3.167.112.45, ...
Connecting to huggingface.co (huggingface.co)|3.167.112.96|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs.hf.co/repos/a4/00/a400d3407dcb6ba1378f2783695f545ab7ba55b1b8bbea86f0eb7ab8793c3a98/036e6e2bd49697511f4f8b8cb5ee465f93025f7a69a145eadeb9a881ace9b18d?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27model.safetensors%3B+filename%3D%22model.safetensors%22%3B&Expires=1753410513&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTc1MzQxMDUxM319LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy5oZi5jby9yZXBvcy9hNC8wMC9hNDAwZDM0MDdkY2I2YmExMzc4ZjI3ODM2OTVmNTQ1YWI3YmE1NWIxYjhiYmVhODZmMGViN2FiODc5M2MzYTk4LzAzNmU2ZTJiZDQ5Njk3NTExZjRmOGI4Y2I1ZWU0NjVmOTMwMjVmN2E2OWExNDVlYWRlYjlhODgxYWNlOWIxOGQ%7EcmVzcG9uc

>>> 'model.safetensors' 다운로드 완료.
>>> '4x-UltraSharp.pth'이(가) 이미 존재합니다.

--- 모든 모델 다운로드가 완료되었습니다. ---


. .......... 98%  192M 0s
3813300K .......... .......... .......... .......... .......... 98%  337M 0s
3813350K .......... .......... .......... .......... .......... 98%  293M 0s
3813400K .......... .......... .......... .......... .......... 98%  261M 0s
3813450K .......... .......... .......... .......... .......... 98%  263M 0s
3813500K .......... .......... .......... .......... .......... 98%  284M 0s
3813550K .......... .......... .......... .......... .......... 99%  205M 0s
3813600K .......... .......... .......... .......... .......... 99%  146M 0s
3813650K .......... .......... .......... .......... .......... 99%  197M 0s
3813700K .......... .......... .......... .......... .......... 99%  191M 0s
3813750K .......... .......... .......... .......... .......... 99%  218M 0s
3813800K .......... .......... .......... .......... .......... 99%  210M 0s
3813850K .......... .......... .......... .......... .......... 99%  214M 0s
3813900K .......... .......... .......... ........